# Study case for conventional power systems
## Loading Packages necessary for simulation¶

In [2]:
using Pkg;
Pkg.instantiate();
cd(@__DIR__);
using PowerDynamics;
using Plots;
using OrdinaryDiffEq: ODEProblem, Rodas4, solve;
using DataFrames;
include("plotting.jl");
include("helpers.jl");
include("simulate_pd.jl");

  Updating registry at `~/.julia/registries/General`
  Updating git-repo `https://github.com/JuliaRegistries/General.git`
Fetching: [========================================>]  100.0 %.0 %

## Model Building

In [ ]:
node_list=[
    SwingEqLVS(H=5.148, P=2.32, D=0.0063662, Ω=314.159, Γ=2, V=1), #node 1
    SlackAlgebraic(U=1), #node 2
    SwingEqLVS(H=6.54, P=-0.942, D=0.0063662, Ω= 314.159, Γ=2, V=1), #node 3
    PQAlgebraic(P=-0.478, Q=-0.0), #node 4
    PQAlgebraic(P=-0.076, Q=-0.016), #node 5
    SwingEqLVS(H=5.06, P=-0.112, D=0.0063662, Ω=314.159, Γ=2, V=1), #node 6
    PQAlgebraic(P=0, Q=0), #node 7
    SwingEqLVS(H=5.06, P=0.0, D=0.0063662, Ω=314.159, Γ=2, V=1), #node 8
    PQAlgebraic(P=-0.295,Q= -0.166), #node 9
    PQAlgebraic(P=-0.09, Q=-0.058), #node 10
    PQAlgebraic(P=-0.035,Q= -0.018), #node 11
    PQAlgebraic(P=-0.061, Q=-0.016), #node 12
    PQAlgebraic(P=-0.135, Q=-0.058), #node 13
    PQAlgebraic(P=-0.149, Q=-0.05) #node 14
];

In [ ]:
line_list=[
    PiModelLine(from=1, to=2, y=4.99913-15.2631im, y_shunt_km=1/2*0.0528*1im, y_shunt_mk=1/2*0.0528*1im), # line 1
    PiModelLine(from=1, to=5, y=1.0259-4.23498im, y_shunt_km=1/2*0.0492*1im, y_shunt_mk=1/2*0.0492*1im),  # line 2
    PiModelLine(from=2, to=3, y=1.13502-4.78186im, y_shunt_km=1/2*0.0438*1im, y_shunt_mk=1/2*0.0438*1im), # line 3
    PiModelLine(from=2, to=4, y=1.68603-5.11584im, y_shunt_km=1/2*0.0374*1im, y_shunt_mk=1/2*0.0374*1im), # line 4
    PiModelLine(from=2, to=5, y=1.70114-5.19393im, y_shunt_km=1/2*0.034*1im, y_shunt_mk=1/2*0.034*1im), # line 5
    PiModelLine(from=3, to=4, y=1.98598-5.06882im, y_shunt_km=1/2*0.0346*1im, y_shunt_mk=1/2*0.0346*1im), # line 6
    PiModelLine(from=4, to=5, y=6.84098-21.5786im, y_shunt_km=1/2*0.0128*1im, y_shunt_mk=1/2*0.0128*1im), # line 7
    PiModelLine(from=4, to=7, y=0.0-4.78194im, y_shunt_km=0,y_shunt_mk=0), # line 8
    PiModelLine(from=4, to=9, y=0.0-1.79798im, y_shunt_km=0,y_shunt_mk=0), # line 9
    PiModelLine(from=5, to=6, y=0.0-3.96794im, y_shunt_km=0,y_shunt_mk=0), # line 10
    PiModelLine(from=6, to=11,y=1.95503-4.09407im, y_shunt_km=0,y_shunt_mk=0), # line 11
    PiModelLine(from=6, to=12, y=1.52597-3.17596im, y_shunt_km=0,y_shunt_mk=0), # line 12
    PiModelLine(from=6, to=13, y=3.09893-6.10276im, y_shunt_km=0,y_shunt_mk=0), # line 13
    PiModelLine(from=7, to=8, y=0.0-5.67698im, y_shunt_km=0,y_shunt_mk=0), # line 14
    PiModelLine(from=7, to=9, y=0.0-9.09008im, y_shunt_km=0,y_shunt_mk=0), # line 15
    PiModelLine(from=9, to=10, y=3.90205-10.3654im, y_shunt_km=0,y_shunt_mk=0), # line 16
    PiModelLine(from=9, to=14, y=1.42401-3.02905im, y_shunt_km=0,y_shunt_mk=0), # line 17
    PiModelLine(from=10, to=11,y= 1.88088-4.40294im, y_shunt_km=0,y_shunt_mk=0), # line 18
    PiModelLine(from=12, to=13, y=2.48902-2.25197im, y_shunt_km=0,y_shunt_mk=0), # line 19
    PiModelLine(from=13, to=14, y=1.13699-2.31496im, y_shunt_km=0,y_shunt_mk=0) # line 20
];

In [ ]:
powergrid = PowerGrid(node_list,line_list)
operationpoint = find_operationpoint(powergrid);

In [5]:
# reduce inertia of power grid
nodes_reduced_inertia = [1,3,6,8]
scaling_factor=0.3
powergrid_inertia_reduced = change_inertia(scaling_factor,nodes_reduced_inertia,powergrid);

## Line tripping

In [ ]:
disturbed_nodes=[6,12]
simulation_time=(0.,5.)

In [ ]:
sol_lf,result_lf,faulty_grid= simulate_linefault(disturbed_nodes,powergrid,operationpoint,simulation_time);
sol_lf2,result_lf2,faulty_grid2= simulate_linefault(disturbed_nodes,powergrid_inertia_reduced,operationpoint,simulation_time);

In [7]:
plot_res_compare(result_lf,result_lf2,faulty_grid,faulty_grid2,disturbed_nodes[1])

In [11]:
# RoCoF and nadir for the base power grid with a line fault
table = determine_rocof_nadir(faulty_grid,sol_lf,simulation_time[2])

4×3 DataFrame
│ Row │ node  │ RoCoF     │ nadir      │
│     │ Int64 │ Float64   │ Float64    │
├─────┼───────┼───────────┼────────────┤
│ 1   │ 1     │ 0.0319249 │ 0.00169993 │
│ 2   │ 3     │ 0.118247  │ 0.00879357 │
│ 3   │ 6     │ 0.183856  │ 0.0148691  │
│ 4   │ 8     │ 0.127534  │ 0.0109672  │

In [10]:
# RoCoF and nadir for the reduced inerta power grid with a line fault
table2 = determine_rocof_nadir(faulty_grid2,sol_lf2,simulation_time[2])

4×3 DataFrame
│ Row │ node  │ RoCoF    │ nadir      │
│     │ Int64 │ Float64  │ Float64    │
├─────┼───────┼──────────┼────────────┤
│ 1   │ 1     │ 0.100054 │ 0.00289603 │
│ 2   │ 3     │ 0.342524 │ 0.0139639  │
│ 3   │ 6     │ 0.589455 │ 0.0258455  │
│ 4   │ 8     │ 0.425102 │ 0.0198033  │

## Sudden Loss of Load

In [ ]:
timespan= (0.,5);
tspan_fault = (0.5,5);
disturbed_node=4;
powergrid = PowerGrid(node_list, line_list);
operationpoint = find_operationpoint(powergrid);
pd = PowerPerturbation(node_number=disturbed_node,fraction=0.5, tspan_fault=tspan_fault);

In [ ]:
sol_pd,result_pd = simulate_pd(pd,powergrid,operationpoint,timespan)
plot_res(result_pd,powergrid,disturbed_node)

In [ ]:
determine_rocof_nadir(powergrid,sol_pd,timespan[2],timespan)